In [ ]:
ขั้นตอนการติดตั้ง FastAPI สำหรับใช้งานรัน LLM บนเครื่องลูกมีดังนี้ครับ:

## 1\. เตรียมสภาพแวดล้อม (Environment Setup)

1.  **ติดตั้ง Python:** ตรวจสอบให้แน่ใจว่าได้ติดตั้ง **Python** บนเครื่องลูกแล้ว (เวอร์ชัน 3.7 ขึ้นไป) สามารถดาวน์โหลดได้จาก [python.org](https://www.python.org/)
2.  **เปิด Command Prompt/PowerShell:** เปิด Terminal บน Windows โดยกดปุ่ม **Windows + R** แล้วพิมพ์ `cmd` หรือ `powershell` แล้วกด Enter

-----

## 2\. สร้าง Virtual Environment (แนะนำ)

การสร้าง Virtual Environment จะช่วยให้คุณจัดการไลบรารีของโปรเจกต์ได้อย่างเป็นระเบียบและไม่รบกวนการทำงานของ Python หลักในระบบ

  * รันคำสั่งเพื่อสร้าง Virtual Environment:
    ```
    python -m venv myenv
    ```
  * รันคำสั่งเพื่อ Activate Virtual Environment:
      * บน Windows (Command Prompt):
        ```
        myenv\Scripts\activate
        ```
      * บน Windows (PowerShell):
        ```
        .\myenv\Scripts\Activate.ps1
        ```

-----

## 3\. ติดตั้ง FastAPI และ Uvicorn

**FastAPI** คือ Web Framework ส่วน **Uvicorn** คือ ASGI server ที่ใช้รัน FastAPI

  * ใน Virtual Environment ที่ Activate อยู่ ให้รันคำสั่งเพื่อติดตั้งทั้งสองไลบรารี:
    ```
    pip install "fastapi[all]" uvicorn
    ```
      * `fastapi[all]` จะติดตั้งไลบรารีที่จำเป็นทั้งหมด รวมถึง Pydantic ซึ่งใช้สำหรับทำ Data Validation ด้วย

-----

## 4\. ติดตั้งไลบรารีสำหรับ LLM

ติดตั้งไลบรารีที่จำเป็นสำหรับการรันโมเดล LLM เช่น Hugging Face Transformers และ PyTorch

  * รันคำสั่งเพื่อติดตั้ง:
    ```
    # pip install transformers torch
    pip install torch torchvision --index-url https://download.pytorch.org/whl/cu129
    pip install transformers
    ```
      * ถ้าต้องการใช้การประมวลผลบนการ์ดจอ NVIDIA **RTX 5060 Ti** ให้ติดตั้ง PyTorch ที่รองรับ CUDA โดยไปที่ [PyTorch Get Started](https://pytorch.org/get-started/locally/) และเลือกคำสั่งติดตั้งที่เหมาะสมกับระบบของคุณ

-----

## 5\. สร้างไฟล์ API Server

สร้างไฟล์ Python ชื่อ `main.py` และใส่โค้ดสำหรับ FastAPI

  * ตัวอย่างโค้ด:
    ```python
    # main.py

    from fastapi import FastAPI, HTTPException
    from pydantic import BaseModel
    import torch
    from transformers import AutoModelForCausalLM, AutoTokenizer

    # สร้าง instance ของ FastAPI
    app = FastAPI()

    # โหลดโมเดล LLM และ Tokenizer
    # ตัวอย่างนี้ใช้โมเดล Mistral-7B-Instruct-v0.1
    # คุณสามารถเปลี่ยนเป็นโมเดลอื่นที่ต้องการได้
    try:
        model_name = "gpt2"
        tokenizer = AutoTokenizer.from_pretrained(model_name)
        model = AutoModelForCausalLM.from_pretrained(model_name)
    except Exception as e:
        raise HTTPException(status_code=500, detail=f"Failed to load model: {e}")

    # สร้าง Pydantic model สำหรับ Request Body
    class PromptRequest(BaseModel):
        prompt: str
        max_new_tokens: int = 100

    @app.post("/generate/")
    def generate_text(request: PromptRequest):
        try:
            inputs = tokenizer(request.prompt, return_tensors="pt")
            outputs = model.generate(**inputs, max_new_tokens=request.max_new_tokens)
            generated_text = tokenizer.decode(outputs[0], skip_special_tokens=True)
            return {"generated_text": generated_text}
        except Exception as e:
            raise HTTPException(status_code=500, detail=f"Generation failed: {e}")

    # ถ้าใช้ใน production, ใช้ uvicorn รันโดยตรง
    # if __name__ == "__main__":
    #     import uvicorn
    #     uvicorn.run(app, host="0.0.0.0", port=8000)
    ```

-----

## 6\. รัน API Server

  * ใน Terminal ให้รันคำสั่งเพื่อเริ่ม Uvicorn server:
    ```
    uvicorn main:app --host 0.0.0.0 --port 8000
    ```
      * `main:app` คือการบอกให้ Uvicorn รัน app instance ที่อยู่ในไฟล์ `main.py`
      * `--host 0.0.0.0` ทำให้เซิร์ฟเวอร์สามารถเข้าถึงได้จากทุก IP Address ในเครือข่ายเดียวกัน
      * `--port 8000` กำหนดพอร์ตที่ใช้

-----

## 7\. ทดสอบ API (จากเครื่องหลัก)

1.  **เปิดเบราว์เซอร์** บนเครื่องหลักแล้วไปที่ `http://<IP_เครื่องลูก>:8000/docs` เพื่อดูหน้าเอกสาร **Swagger UI** ของ FastAPI
2.  คุณสามารถทดสอบ Endpoint `/generate/` ได้โดยตรงจากหน้านี้
3.  หรือใช้โค้ด Python เพื่อส่งคำขอ POST ไปยัง API
    ```python
    import requests
    import json

    url = "http://<IP_เครื่องลูก>:8000/generate/"
    headers = {"Content-Type": "application/json"}
    payload = {"prompt": "What is the capital of Thailand?", "max_new_tokens": 50}

    response = requests.post(url, headers=headers, data=json.dumps(payload))
    print(response.json())
    ```